In [23]:
import os
import json
import inspect
import sqlite3
import requests
import strategy
import numpy as np
import pandas as pd
import binance_data
from enum import Enum
import indicators as ta
from datetime import datetime
from matplotlib import pyplot as plt

In [24]:
symbol_list = ["BTCUSDT"]
interval = binance_data.Interval.Minute_30.value
start_time = binance_data.datetime_timestamp(2021, 10, 1, 0, 0, 0)
end_time = binance_data.datetime_timestamp(2022, 6, 30, 0, 0, 0)
column_name = ["Open time", "Open", "High", "Low", "Close", "Volume", "Close time", "Quote asset volume", 
       "Number of trades", "Taker buy base asset volume", "Taker buy quote asset volume", "Ignore"]
Data = pd.DataFrame(binance_data.get_klines("BTCUSDT", interval, start_time, end_time), columns = column_name)
col = ["Open time", "Open", "High", "Low", "Close", "Volume"]
df = Data[col]
df = df.rename({"Open time": 'Date'}, axis=1)
df.Date = (df["Date"] / 1000).apply(datetime.fromtimestamp)
df = df.astype({col: float for col in df.columns[1:]})

2021-10-01 00:00:00 2021-10-21 19:30:00 1000
2021-10-21 20:00:00 2021-11-11 15:30:00 1000
2021-11-11 16:00:00 2021-12-02 11:30:00 1000
2021-12-02 12:00:00 2021-12-23 07:30:00 1000
2021-12-23 08:00:00 2022-01-13 03:30:00 1000
2022-01-13 04:00:00 2022-02-02 23:30:00 1000
2022-02-03 00:00:00 2022-02-23 19:30:00 1000
2022-02-23 20:00:00 2022-03-16 15:30:00 1000
2022-03-16 16:00:00 2022-04-06 11:30:00 1000
2022-04-06 12:00:00 2022-04-27 07:30:00 1000
2022-04-27 08:00:00 2022-05-18 03:30:00 1000
2022-05-18 04:00:00 2022-06-07 23:30:00 1000
2022-06-08 00:00:00 2022-06-28 19:30:00 1000
2022-06-28 20:00:00 2022-06-30 00:00:00 57
------ BTCUSDT ------ 2021-10-01 00:00:00 - 2022-06-30 00:00:00


In [25]:
from bokeh.io import show, output_file, output_notebook, curdoc
from bokeh.plotting import figure, show
from bokeh.models import SingleIntervalTicker, LinearAxis, ColumnDataSource, HoverTool, HoverTool, CustomJS, Legend, Range1d
from bokeh.palettes import Spectral4, Spectral, Dark2, RdYlBu, Viridis, Category10
from bokeh.models import LinearAxis, Range1d, Legend, CustomJS
from bokeh.layouts import column
output_notebook()

Loading BokehJS ...

In [5]:
Dark2

{3: ('#1b9e77', '#d95f02', '#7570b3'),
 4: ('#1b9e77', '#d95f02', '#7570b3', '#e7298a'),
 5: ('#1b9e77', '#d95f02', '#7570b3', '#e7298a', '#66a61e'),
 6: ('#1b9e77', '#d95f02', '#7570b3', '#e7298a', '#66a61e', '#e6ab02'),
 7: ('#1b9e77',
  '#d95f02',
  '#7570b3',
  '#e7298a',
  '#66a61e',
  '#e6ab02',
  '#a6761d'),
 8: ('#1b9e77',
  '#d95f02',
  '#7570b3',
  '#e7298a',
  '#66a61e',
  '#e6ab02',
  '#a6761d',
  '#666666')}

In [26]:
class Backtest():
    def __init__(self, data, strategy, parameter, commission = 0.004, capital = 100000, riskfree_rate = 0.01):
        self.df = data.copy()
        self.strategy = strategy
        self.parameter = parameter
        self.summary = {}
        self.trade_list = []
        self.commission = commission
        self.capital = capital
        self.rate = riskfree_rate
        self.trade_cost = 0
    def get_position(self, entry, exit = pd.DataFrame([])):
        """
        Get Position
        
        Parameters
        ----------
        entry: entry signal
        exit: exit signal 
        """
        if exit.empty:
            exit = pd.DataFrame(0, index = range(len(entry)), columns = ["exit"])
        position = entry.copy()
        for i in range(1, len(entry)):
            position.iloc[i] = (entry.iloc[i] if entry.iloc[i] else position.iloc[i - 1]) * (exit.iloc[i] == 0)
        position = position.shift(1)
        return position.fillna(0)
    
    def strategy_performance(self):
        """
        Calculate Strategy performance
        """
        self.df["Entry"], self.df["Exit"] = self.strategy(self.df, self.parameter)
        self.df["Position"] = self.get_position(self.df.Entry, self.df.Exit)
        self.df["PnL"] = ((self.df.Close - self.df.Close.shift(1)) * self.df.Position).cumsum()
        self.df[["Equity_long", "Equity_short", "Equity"]] = pd.DataFrame(self.capital, index = range(len(self.df)), columns = ["l", "s", "all"])
        self.df[["Run_up", "Drawdown"]] = pd.DataFrame(0, index = range(len(self.df)), columns = ["r", "d"])        
        self.trade_list = [] # type, quantity, entry_time, entry_price, exit_time, exit_price, profit, profit_cum, entry_high, entry_low, MaxDrawdown
        entry_info = [] # position, entry_time, entry_price, entry_high, entry_low
        equity_max, equity_min = self.capital, self.capital
        trade_commission = [0, 0, 0] # Equity, Equity long, Equity short
        profit, profit_cum = 0, 0
        
        for i in range(1, len(self.df)):
            ########################## position != 0 ##########################
            if self.df.Position[i]:
                ########################## first entry ##########################
                if self.df.Position[i - 1] == 0:
                    entry_info.append([self.df.Position[i], self.df.Date[i], self.df.Close[i - 1], self.df.High[i], self.df.Low[i]])                    
                    self.trade_cost += abs(self.df.Position[i]) * self.df.Close[i - 1] * self.commission
                    trade_commission = [abs(self.df.Position[i]) * self.df.Close[i - 1] * self.commission, 
                                        abs(self.df.Position[i]) * self.df.Close[i - 1] * self.commission if self.df.Position[i] > 0 else 0,                                
                                        abs(self.df.Position[i]) * self.df.Close[i - 1] * self.commission if self.df.Position[i] < 0 else 0]
                   
                ########################## same sign ##########################
                elif self.df.Position[i - 1] * self.df.Position[i] > 0:
                    ########################## raise quantity ##########################
                    if abs(self.df.Position[i]) > abs(self.df.Position[i - 1]):
                        entry_info.append([(self.df.Position[i] - self.df.Position[i - 1]), self.df.Date[i], self.df.Close[i - 1], self.df.High[i], self.df.Low[i]])
                        self.trade_cost += abs(self.df.Position[i] - self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission
                        trade_commission = [abs(self.df.Position[i] - self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission,                                      
                                            abs(self.df.Position[i] - self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission if (self.df.Position[i] - self.df.Position[i - 1]) > 0 else 0, 
                                            abs(self.df.Position[i] - self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission if (self.df.Position[i] - self.df.Position[i - 1]) < 0 else 0]
                    ########################## partial exit ||| todo ##########################
                    elif abs(self.df.Position[i]) < abs(self.df.Position[i - 1]):
                        self.trade_list.append()
                
                ########################## opposite position ##########################
                else:
                    for entry in entry_info:
                        profit = (self.df.Close[i - 1] - entry[2]) * entry[0] - (self.df.Close[i - 1] + entry[2]) * self.commission * abs(entry[0])
                        profit_cum += profit
                        self.trade_list.append((np.sign(entry[0]), abs(entry[0]), entry[1], entry[2], self.df.Date[i], self.df.Close[i - 1], profit, profit_cum, entry[3], entry[4], 
                                                min(0, (entry[4] - entry[2] if entry[0] > 0 else entry[3] - entry[2]) * entry[0]) - (self.df.Close[i - 1] + entry[2]) * self.commission * abs(entry[0])))
                    entry_info = []
                    entry_info.append([self.df.Position[i], self.df.Date[i], self.df.Close[i - 1], self.df.High[i], self.df.Low[i]])
                    self.trade_cost += abs(self.df.Position[i] - self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission
                    trade_commission = [abs(self.df.Position[i] - self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission,                                  
                                        abs(self.df.Position[i] if self.df.Position[i] > 0 else self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission, 
                                        abs(self.df.Position[i] if self.df.Position[i] < 0 else self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission]
               
                ########################## calculate all ##########################
                equity_change = self.df.Position[i] * (self.df.Close[i] - self.df.Close[i - 1])
                self.df.loc[i, "Equity_long"] = self.df.Equity_long[i - 1] + (equity_change if self.df.Position[i] > 0 else 0) - trade_commission[1]
                self.df.loc[i, "Equity_short"] = self.df.Equity_short[i - 1] + (equity_change if self.df.Position[i] < 0 else 0) - trade_commission[2]
                self.df.loc[i, "Equity"] = self.df.Equity[i - 1] + equity_change - trade_commission[0]
                trade_commission = [0, 0, 0]
                equity_max = max(equity_max, self.df.Equity[i])
                equity_min = min(equity_min, self.df.Equity[i])
                self.df.loc[i, "Run_up"] = self.df.Equity[i] - equity_min
                self.df.loc[i, "Drawdown"] = self.df.Equity[i] - equity_max
                for entry in entry_info:
                    entry[3] = max(self.df.High[i], entry[3])
                    entry[4] = min(self.df.Low[i], entry[4])
               
            ########################## Position == 0 ##########################
            else: 
                if self.df.Position[i - 1]:
                    for entry in entry_info:
                        profit = (self.df.Close[i - 1] - entry[2]) * entry[0] - (self.df.Close[i - 1] + entry[2]) * self.commission * abs(entry[0])
                        profit_cum += profit
                        self.trade_list.append((np.sign(entry[0]), abs(entry[0]), entry[1], entry[2], self.df.Date[i], self.df.Close[i - 1], profit, profit_cum, entry[3], entry[4], 
                                                min(0, (entry[4] - entry[2] if entry[0] > 0 else entry[3] - entry[2]) * entry[0]) - (self.df.Close[i - 1]) * self.commission * abs(entry[0])))
                    entry_info = []
                    self.trade_cost += abs(self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission
                    self.df.loc[i, "Equity"] -= abs(self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission
                    self.df.loc[i, "Equity_long"] -= abs(self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission if self.df.Position[i - 1] > 0 else 0
                    self.df.loc[i, "Equity_short"] -= abs(self.df.Position[i - 1]) * self.df.Close[i - 1] * self.commission if self.df.Position[i - 1] < 0 else 0
                self.df.loc[i, ["Equity_long", "Equity_short", "Equity", "Run_up", "Drawdown"]] = self.df.loc[i - 1, ["Equity_long", "Equity_short", "Equity", "Run_up", "Drawdown"]]
        ########################## entry_info isn't empty on last day ##########################
        if entry_info:
            for entry in entry_info:
                profit = (self.df.Close[i] - entry[2]) * entry[0] - (self.df.Close[i] + entry[2]) * self.commission * abs(entry[0])
                profit_cum += profit
                self.trade_list.append((np.sign(entry[0]), abs(entry[0]), entry[1], entry[2], self.df.Date[i], self.df.Close[i], profit, profit_cum, entry[3], entry[4], 
                                        min(0, ((entry[4] - entry[2]) if entry[0] > 0 else (entry[3] - entry[2])) * entry[0]) - (self.df.Close[i] + entry[2]) * self.commission * abs(entry[0])))
            entry_info = []
            self.trade_cost += abs(self.df.Position[i]) * self.df.Close[i] * self.commission
            self.df.loc[i, "Equity"] -= abs(self.df.Position[i]) * self.df.Close[i] * self.commission
            self.df.loc[i, "Equity_long"] -= abs(self.df.Position[i]) * self.df.Close[i] * self.commission if self.df.Position[i] > 0 else 0
            self.df.loc[i, "Equity_short"] -= abs(self.df.Position[i]) * self.df.Close[i] * self.commission if self.df.Position[i] < 0 else 0
        self.trade_list = pd.DataFrame(self.trade_list, columns = ["Type", "Quantity", "EntryTime", "EntryPrice", "ExitTime", "ExitPrice", 
                                                                   "Profit", "ProfitCum", "EntryHigh", "EntryLow", "Drawdown"])
        self.trade_list["MFE"] = pd.concat([(self.trade_list.EntryHigh - self.trade_list.EntryPrice) * self.trade_list.Type, (self.trade_list.EntryLow - self.trade_list.EntryPrice) * self.trade_list.Type], axis = 1).max(axis = 1)
        self.trade_list["MAE"] = pd.concat([(self.trade_list.EntryHigh - self.trade_list.EntryPrice) * self.trade_list.Type, (self.trade_list.EntryLow - self.trade_list.EntryPrice) * self.trade_list.Type], axis = 1).min(axis = 1)
        self.trade_list["Size"] = self.trade_list.Type * self.trade_list.Quantity
        self.summary = self.trade_summary(self.df, self.trade_list)
        
        return self.summary
    
    def trade_summary(self, data, tradelist):
        """
        Strategy Performance Summary
        """
        summary = {}
        summary["Net Profit"] = data.Equity.iloc[-1] - self.capital
        summary["Gross Profit"] = tradelist.Profit[tradelist.Profit > 0].sum()
        summary["Gross Loss"] = tradelist.Profit[tradelist.Profit <= 0].sum()
        summary["Commission"] = self.trade_cost
        summary["Max Drawdown"] = data.Drawdown.max()
        summary["Max Drawdown Date"] = str(data.Date[data.Drawdown == data.Drawdown.max()].values[0])
        summary["Profit Factor"] = summary["Gross Profit"] / -summary["Gross Loss"]
        summary["Win Rate"] = (tradelist.Profit > 0).sum() / len(tradelist)
        # Not correct, need to  annualize the return and standard deviation
        summary["Sharpe Ratio"] = (tradelist.Profit.mean() - self.rate) / tradelist.Profit.std()
        summary["Sortino Ratio"] = (tradelist.Profit.mean() - self.rate) / tradelist.Profit[tradelist.Profit <= 0].std()
        summary["Calmar Ratio"] = tradelist.Profit.mean() / data.Drawdown.min()
        
        return summary

    def plot(self): # Equity curve, MAE / profit, drawdown, MAE / trade count, 
        None
        
    def technical_analysis(self): # plot ta and OHLC graph
        None
        
    def optimization(self):
        None
        

In [27]:
para = {"num": 5, "ratio": 1}
bt = Backtest(df, strategy.ketlner, para, commission = 0)

In [28]:
bt.strategy_performance()

{'Net Profit': 37806.210000000254,
 'Gross Profit': 116133.84999999999,
 'Gross Loss': -78327.64,
 'Commission': 0.0,
 'Max Drawdown': 0.0,
 'Max Drawdown Date': '2021-10-01T00:00:00.000000000',
 'Profit Factor': 1.482667548773332,
 'Win Rate': 0.421875,
 'Sharpe Ratio': 0.12639257933292308,
 'Sortino Ratio': 0.35719902821491795,
 'Calmar Ratio': -0.015680590590988266}

In [36]:
df = bt.df[:100].copy()
df["index"] = df.index
df_ = ColumnDataSource(df)
inc = df.Close > df.Open
dec = df.Open > df.Close
inc_df = ColumnDataSource(df[inc])
dec_df = ColumnDataSource(df[dec])
TOOLS = "xpan, pan, xwheel_zoom,box_zoom,reset,save"
w = (df["index"].iloc[1] - df["index"].iloc[0]) * 0.8 # half day in ms
y_p_start, y_p_end = df["Low"].min(), df["High"].max()

p = figure(tools=[TOOLS], plot_width=800, title = "Candlestick", y_range = (y_p_start, y_p_end), 
           x_range = Range1d(df["index"].iloc[0], df["index"].iloc[-1], bounds = 'auto', min_interval=10)) # x_range = (df["index"].iloc[0], df["index"].iloc[-1]))
p.grid.grid_line_alpha=0.3

p.segment("index", "High", "index", "Low", color="black", source = df_)
p.vbar("index", w, "Open", "Close", fill_color="#D5E1DD", line_color="black", source=inc_df)
p.vbar("index", w, "Open", "Close", fill_color="#F2583E", line_color="black", source=dec_df)



###### custom js ######

callback = """
if (!window._bt_scale_range) {
    window._bt_scale_range = function (range, min, max, pad) {
        "use strict";
        if (min !== Infinity && max !== -Infinity) {
            pad = pad ? (max - min) * .03 : 0;
            range.start = min - pad;
            range.end = max + pad;
        } else console.error('backtesting: scale range error:', min, max, range);
    };
}
    /**
     * @variable cb_obj `fig_ohlc.x_range`.
     * @variable source `ColumnDataSource`
     */
    "use strict";
    let i = Math.max(Math.floor(p.x_range.start), 0),
        j = Math.min(Math.ceil(p.x_range.end), source.data['High'].length);
    let max = Math.max.apply(null, source.data['High'].slice(i, j)),
        min = Math.min.apply(null, source.data['Low'].slice(i, j));
    _bt_scale_range(p.y_range, min, max, true);
"""
# callback = """
# let i = Math.max(Math.floor(p.x_range.start), 0),
# j = Math.min(Math.ceil(p.x_range.end), source.data['High'].length);
# let max = Math.max.apply(null, source.data['High'].slice(i, j));
# p.y_range.end = max;
# """


p2 = figure(x_axis_type="datetime", tools=p.tools, plot_width=800,plot_height = 200 ,title = "Candlestick", x_range = p.x_range, toolbar_location=None)
p2.segment("index", "High", "index", "Low", color="red", source = df_)  

p3 = figure(x_axis_type="datetime", tools=p.tools, plot_width=800,plot_height = 200, title = "Candlestick", x_range = p.x_range, toolbar_location=None)
p3.segment("index", "High", "index", "Low", color="red", source = df_)  

p.x_range.js_on_change("start", CustomJS(args=dict(p = p, source=df_), code=callback))
p.y_range.js_on_change("end", CustomJS(args=dict(p = p, source=df_), code=callback))
p.xaxis.major_label_overrides = {i: str(date).replace(" ", "\n") for i, date in enumerate(df["Date"])}
# p2.x_range.js_on_change("start", CustomJS(args=dict(p = p2, source=df_), code=callback))
# p2.x_range.js_on_event("zoom", CustomJS(args=dict(p = p2, source=df_), code=callback))
show(column(p, p2, p3))
# show(p)

In [11]:
df_.data

{'level_0': array([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16,
        17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33,
        34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50,
        51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67,
        68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84,
        85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99],
       dtype=int64),
 'index': array([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16,
        17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33,
        34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50,
        51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67,
        68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84,
        85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99],
       dtype=int64),
 'Date': array(['2021-10-01T00:00:00.000

In [20]:
from bokeh.models import FactorRange


In [40]:
df = bt.df.copy()
trade_l = bt.trade_list.copy()

In [41]:
ta_list = ["MA5", "MA10"]
df["MA5"] = ta.MA(df.Close, 5)
df["MA10"] = ta.MA(df.Close, 10)
capital = 100000

In [50]:
########################## theme ##########################
curdoc().theme = 'contrast'

########################## set figure ##########################

df["index"] = df.index
symbol = "BTCUSDT_15m"
title = symbol + " / " + strategy.ketlner.__name__ # self.strategy.__name__
y_p_start, y_p_end = df["Close"].min() * 0.95, df["Close"].max() * 1.05
y_e_start, y_e_end = df[["Equity", "Equity_long", "Equity_short"]].min().min() * 0.995, df[["Equity", "Equity_long", "Equity_short"]].max().max() * 1.005
y_t_start, y_t_end = trade_l.Drawdown.min() * 1.2, trade_l.Profit.max() * 1.1
w = (df["index"].iloc[1] - df["index"].iloc[0]) * 0.8 

p_price  = figure(title = title, y_range = (y_p_start, y_p_end), sizing_mode = "stretch_width", plot_width = 1000, 
                  plot_height = 500, toolbar_location = "above", y_axis_label = "Price", x_axis_type = "datetime", 
                  tools = ["xpan, xwheel_zoom, xbox_zoom, reset, save"], active_scroll = "xwheel_zoom", 
                  background_fill_alpha = 0.9)
p_equity = figure(x_range = p_price.x_range, y_range = (y_e_start, y_e_end), sizing_mode = "stretch_width", 
                  toolbar_location = None, y_axis_label = "Equity", x_axis_type = "datetime", plot_height = 250, 
                  tools = ["xpan, xwheel_zoom, xbox_zoom, reset, save"], active_scroll = "xwheel_zoom", 
                  background_fill_alpha = 0.9)
p_trade    = figure(x_range = p_price.x_range, y_range = (y_t_start, y_t_end), sizing_mode = "stretch_width",
                  toolbar_location = None, y_axis_label = "Profit / Drawdown", plot_height = 250, 
                  tools = ["xpan, xwheel_zoom, xbox_zoom, reset, save"], active_scroll = "xwheel_zoom",
                  background_fill_alpha = 0.9) 

hover_price_items = [("Date", "@Date{%Y-%m-%d %H:%M:%S}"), ("O", "@Open{0.0[00000]}"), ("H", "@High{0.0[00000]}"), 
                       ("L", "@Low{0.0[00000]}"), ("C", "@Close{0.0[00000]}"), ("Vol", "@Volume{0.0[00000]}")]
hover_equity_items = [("Date", "@Date{%Y-%m-%d %H:%M:%S}"), ("Equity", "@Equity{0.0[00000]}"), 
                        ("Equity_Long", "@Equity_long{0.0[00000]}"), ("Equity_Short", "@Equity_short{0.0[00000]}"), 
                        ("Drawdown", "@Drawdown{0.0[00000]}")]
hover_trade_items = [("Date", "@ExitTime{%Y-%m-%d %H:%M:%S}"), ("Size", "@Size"), ("PNL", "@Profit{0.0[00000]}"), 
                     ("Drawdown", "@Drawdown{0.0[00000]}")]

########################## p_price render ##########################
    # OHLC graph
df_source = ColumnDataSource(df)
inc_source = ColumnDataSource(df[["index", "Open", "High", "Low", "Close"]][df.Close > df.Open])
dec_source = ColumnDataSource(df[["index", "Open", "High", "Low", "Close"]][df.Close <= df.Open])
p_price.segment("index", "High", "index", "Low", color = "#5cad95", source = inc_source)
p_price.segment("index", "High", "index", "Low", color = "#cc331e", source = dec_source)
p_price.vbar("index", w, "Open", "Close", fill_color = "#5cad95", line_color = "#5cad95", source = inc_source)
p_price.vbar("index", w, "Open", "Close", fill_color = "#cc331e", line_color = "#cc331e", source = dec_source)
p_price.xaxis.visible = False
    # set twinx volumn
y_vol_start, y_vol_end = df.Volume.min() * 0.95, df.Volume.max() * 2 # 
p_price.extra_y_ranges = {"vol": Range1d(y_vol_start, y_vol_end)}
r_price = p_price.vbar("index", w, "Volume", y_range_name = "vol", color = "#586d80", alpha = 0.8, source = df_source)
p_price.add_layout(LinearAxis(y_range_name="vol" ,axis_label="Volume"), 'right')    
    # set ta line
ta_legend_item = []
if ta_list:
    for ta_name, color in zip(ta_list, Category10[5 if len(ta_list) < 3 else len(ta_list)]): 
        ta_line = p_price.line(x = "index", y = ta_name, line_width = 1.5, color = color, alpha = 0.7, source = df_source)
        ta_legend_item.append((ta_name, [ta_line]))
        hover_price_items.append((ta_name, "@" + ta_name + "{0.0[00000]}"))
    legend_price = Legend(items = ta_legend_item, label_text_color = "black", background_fill_alpha = 0.02)
    p_price.add_layout(legend_price, "right")
    # todo: add entry and exit

########################## p_equity render ##########################
    # equity graph
df["Equity_pos"] = df.Equity.apply(lambda x: capital if x < capital else x)
df["Equity_neg"] = df.Equity.apply(lambda x: capital if x >= capital else x)
equity_pos_source = ColumnDataSource(df[["index", "Equity_pos"]]) # self.capital
equity_neg_source = ColumnDataSource(df[["index", "Equity_neg"]]) # self.capital
equity_legend_item = []
r_equity_capital = p_equity.line(x = "index", y = capital, line_width = 2.5, color = "#9da49d", alpha = 0.5, source = df_source)
r_equity_long  = p_equity.line(x = "index", y = "Equity_long", line_width = 2, color = "#4c5445", alpha = 0.7, source = df_source)
r_equity_short = p_equity.line(x = "index", y = "Equity_short", line_width = 2, color = "#976666", alpha = 0.7, source = df_source)
r_equity_total_win = p_equity.line(x = "index", y = "Equity_pos", line_width = 1.5, color = "darkseagreen", alpha = 0.7, source = equity_pos_source)
r_equity_total_loss = p_equity.line(x = "index", y = "Equity_neg", line_width = 1.5, color = "#e1aa8d", alpha = 0.7, source = equity_neg_source)
r_equity_total_win_a = p_equity.varea(x = "index", y1 = "Equity_pos", y2 = capital, color = "darkseagreen", alpha = 0.3, source = equity_pos_source)
r_equity_total_loss_a = p_equity.varea(x = "index", y1 = "Equity_neg", y2 = capital, color = "#e1aa8d", alpha = 0.2, source = equity_neg_source)

    # set twinx drawdown
y_dd_start, y_dd_end = (y_e_start - df.Equity.max()) * 1.1, df.Drawdown.max() # 
p_equity.extra_y_ranges = {"mdd": Range1d(y_dd_start, y_dd_end)}
r_equity_dd = p_equity.line(x = "index", y = "Drawdown", line_width = 1.5, color = "indianred", alpha = 0.7, source = df_source, y_range_name="mdd")
r_equity_dd_a = p_equity.varea(x = "index", y1 = "Drawdown", y2 = df.Drawdown.max(), color = "indianred", alpha = 0.3, source = df_source, y_range_name="mdd")
p_equity.add_layout(LinearAxis(y_range_name="mdd" ,axis_label="Max Drawdown"), 'right') 

    # set legend
equity_legend_item = [("Equity", [r_equity_total_win, r_equity_total_loss, r_equity_total_win_a, r_equity_total_loss_a]), 
                      ("Max Drawdown", [r_equity_dd, r_equity_dd_a]), 
                      ("Equity long", [r_equity_long]), ("Equity short", [r_equity_short])]
legend_equity = Legend(items = equity_legend_item, label_text_color = "black", background_fill_alpha = 0.02)
p_equity.add_layout(legend_equity, "right")
r_equity_long.visible = False
r_equity_short.visible = False
p_equity.xaxis.visible = False
p_equity.yaxis.formatter.use_scientific = False

########################## p_trade render ##########################
trade_l["index"] = [df.index[df.Date == exit][0] for exit in trade_l.ExitTime]
trade_l["entry_index"] = [df.index[df.Date == entry][0] for entry in trade_l.EntryTime]
trade_l["size"] = ((trade_l.Profit.abs()) / trade_l.Profit.abs().max()) * 5 + 10
profit_pos_source = ColumnDataSource(trade_l[trade_l.Profit > 0])
profit_neg_source = ColumnDataSource(trade_l[trade_l.Profit <= 0])
r_trade_long_win = p_trade.triangle("index", "Profit", "size", fill_color = "darkseagreen", line_alpha = 0, 
                                    source = ColumnDataSource(trade_l[(trade_l.Profit > 0) & (trade_l.Type == 1)]))
r_trade_long_loss = p_trade.triangle("index", "Profit", "size", fill_color = "indianred", line_alpha = 0, 
                                     source = ColumnDataSource(trade_l[(trade_l.Profit <= 0) & (trade_l.Type == 1)]))
r_trade_short_win = p_trade.inverted_triangle("index", "Profit", "size", fill_color = "darkseagreen", line_alpha = 0,
                                              source = ColumnDataSource(trade_l[(trade_l.Profit > 0) & (trade_l.Type == -1)]))
r_trade_short_loss = p_trade.inverted_triangle("index", "Profit", "size", fill_color = "indianred", line_alpha = 0,
                                               source = ColumnDataSource(trade_l[(trade_l.Profit <= 0) & (trade_l.Type == -1)]))
r_trade_win_dd = p_trade.vbar("index", 3 * w, "Drawdown", "Profit", fill_color = "darkseagreen", fill_alpha = 0.5, line_alpha = 0, source = profit_pos_source)
r_trade_loss_dd = p_trade.vbar("index", 3 * w, "Drawdown", "Profit", fill_color = "indianred", fill_alpha = 0.5, line_alpha = 0, source = profit_neg_source)
r_trade_for_hover = p_trade.circle("index", "Profit", size = "size", fill_alpha = 0, line_alpha = 0, source = ColumnDataSource(trade_l))

    # set legend
trade_legend_item = [("Win trade", [r_trade_long_win, r_trade_short_win]), 
                      ("Loss trade", [r_trade_long_loss, r_trade_short_loss]), 
                      ("Drawdown", [r_trade_win_dd, r_trade_loss_dd])]
legend_trade = Legend(items = trade_legend_item, label_text_color = "black", background_fill_alpha = 0.02)
p_trade.add_layout(legend_trade, "right")
r_trade_win_dd.visible = False
r_trade_loss_dd.visible = False

########################## set hover ##########################
hover_price_tooltips = """<strong><pre style = "color: rgba(255, 255, 255 ,0.7);"><span style = "color: #ae8977;">""" + \
        """\n<span style = "color: #ae8977;">""".join(["</span>: ".join(item) for item in hover_price_items]) + "</pre></strong>"
hover_equity_tooltips = """<strong><pre style = "color: rgba(255, 255, 255 ,0.7);"><span style = "color: #ae8977;">""" + \
        """\n<span style = "color: #ae8977;">""".join(["</span>: ".join(item) for item in hover_equity_items]) + "</pre></strong>"
hover_trade_tooltips = """<strong><pre style = "color: rgba(255, 255, 255 ,0.7);"><span style = "color: #ae8977;">""" + \
        """\n<span style = "color: #ae8977;">""".join(["</span>: ".join(item) for item in hover_trade_items]) + "</pre></strong>"

hover_price = HoverTool(tooltips = hover_price_tooltips, formatters={"@Date": "datetime"}, mode="vline", show_arrow = False)
hover_equity = HoverTool(tooltips = hover_equity_tooltips, formatters={"@Date": "datetime"}, mode="vline", show_arrow = False)
hover_trade = HoverTool(tooltips = hover_trade_tooltips, formatters={"@ExitTime": "datetime"}, mode="vline", show_arrow = False)

callback_hover = CustomJS(args = {'p': p_price}, code = """
                                var tooltips = document.getElementsByClassName("bk-tooltip");
                                for (var i = 0; i < tooltips.length; i++) {
                                    tooltips[i].style.top = '25px'; 
                                    tooltips[i].style.left = '80px'; 
                                    tooltips[i].style["backgroundColor"] = "rgba(0, 0, 0, 0.01)";
                                tooltips[i].style["border"] = "0px";} """)

########################## auto-adjust y_range ##########################
y_range_callback = """
if (!window._bt_scale_range) {
    window._bt_scale_range = function (range, min, max, pad) {
        "use strict";
        if (min !== Infinity && max !== -Infinity) {
            pad = pad ? (max - min) * .03 : 0;
            range.start = min - pad;
            range.end = max + pad;
        } else console.error('backtesting: scale range error:', min, max, range);};}
    /**
     * @variable cb_obj `fig_ohlc.x_range`.
     * @variable source `ColumnDataSource`
     */
    "use strict";
    let i = Math.max(Math.floor(p.x_range.start), 0),
        j = Math.min(Math.ceil(p.x_range.end), source.data['High'].length);
    let max = Math.max.apply(null, source.data['High'].slice(i, j)),
        min = Math.min.apply(null, source.data['Low'].slice(i, j));
    _bt_scale_range(p.y_range, min, max, true);
    p.x_range.start = Math.max(Math.floor(p.x_range.start), Math.floor(- source.data['High'].length * 0.01));
    p.x_range.end = Math.min(Math.ceil(p.x_range.end), Math.floor(source.data['High'].length * 1.01));
"""


p_price.x_range.js_on_change("start", CustomJS(args = dict(p = p_price, source = df_source), code = y_range_callback))
p_price.y_range.js_on_change("end", CustomJS(args = dict(p = p_price, source = df_source), code = y_range_callback))

# set legend & figure
hover_price.renderers = [r_price]
hover_equity.renderers = [r_equity_capital]
hover_trade.renderers = [r_trade_for_hover]
for fig, hov in zip([p_price, p_equity, p_trade], [hover_price, hover_equity, hover_trade]):
    fig.tools.append(hov)
    hov.callback = callback_hover
    fig.grid.grid_line_alpha = 0.05
    fig.legend.click_policy = "hide"
    fig.legend.label_text_font_size = "8pt"
    fig.yaxis.axis_label_text_font_size = "10pt"
    fig.axis.axis_label_text_font_style = "bold"
    fig.yaxis.major_label_text_font_size = "8pt"
p_trade.xaxis.major_label_overrides = {i: str(date).replace(" ", "\n") for i, date in enumerate(df["Date"])}
p_trade.xaxis.major_label_text_font_size = "8pt"

output_notebook()
show(column(p_price, p_equity, p_trade))

Loading BokehJS ...

In [14]:
def technical_chart(json_df):
    # get data
    stock_data = json_df
    df = pd.DataFrame(stock_data['price_df']).reset_index().rename(columns={'index': 'date'})
    df = df.reset_index()
    inc = df.close > df.open
    dec = df.open > df.close
    inc_data = df[inc]
    dec_data = df[dec]
    df_source = ColumnDataSource(df)
    inc_source = ColumnDataSource(inc_data)
    dec_source = ColumnDataSource(dec_data)

    # set hover
    hover = HoverTool(
        tooltips=[
            ("date", "@date"),
            ("close", "@open"),
            ("open", "@close"),
            ("high", "@high"),
            ("low", "@low"),
            ("volume", "@volume")
        ],
        formatters={"@date": "datetime"}
    )

    hover_rsi_kd = HoverTool(
        tooltips=[
            ("date", "@date"),
            ("RSI_12", "@RSI_12"),
            ("RSI_36", "@RSI_36"),
            ("slowk", "@slowk"),
            ("slowd", "@slowd"),

        ],
        formatters={"@date": "datetime"}

    )

    hover_macd = HoverTool(
        tooltips=[
            ("date", "@date"),
            ("macd", "@macd"),
            ("macdsignal", "@macdsignal"),
            ("macdhist", "@macdhist"),
        ],
        formatters={"@date": "datetime"}

    )

    # set figure data
    basic_data = stock_data['basic']
    title = basic_data['stock_id'] + ' ' + basic_data['name'] + ' ' + 'technical_chart'
    x_end = len(df)
    show_init_num = 120
    x_start = x_end - show_init_num
    interval_freq = show_init_num / 12
    y_start = df['close'].min() * 0.95
    y_end = df['close'].max() * 1.05
    p1 = figure(plot_width=1000, title=title, plot_height=500, x_range=(x_start, x_end), y_range=(y_start, y_end),
                tools=[hover, "pan,xwheel_zoom,zoom_out,crosshair,reset,save"], toolbar_location="above" ,y_axis_label="price")
    p2 = figure(plot_width=1000, title='RSI&KD', plot_height=250, x_range=(x_start, x_end),
                background_fill_color="#fafafa", tools=[hover_rsi_kd, "pan,zoom_in,zoom_out,crosshair,reset,save"],
                toolbar_location="above")
    p3 = figure(plot_width=1000, title='MACD', plot_height=250, x_range=(x_start, x_end),
                background_fill_color="#fafafa", tools=[hover_macd, "pan,zoom_in,zoom_out,crosshair,reset,save"],
                toolbar_location="above")

    for fig in [p1, p2, p3]:
        fig.title.text_font_size = '16pt'

        # map dataframe indices to date strings and use as label overrides
        fig.xaxis.major_label_overrides = {
            i: date.strftime('%Y/%m/%d') for i, date in enumerate(pd.to_datetime(df["date"]))
            # pd.date_range(start='3/1/2000', end='1/08/2018')
        }
        fig.xaxis.ticker = SingleIntervalTicker(interval=interval_freq)

    # set k bar chart
    # use the *indices* for x-axis coordinates, overrides will print better labels
    p1.segment('index', 'high', 'index', 'low', color="black", source=df_source)
    p1.vbar('index', 0.5, 'open', 'close', fill_color="#eb2409", line_color="black", source=inc_source)
    p1.vbar('index', 0.5, 'open', 'close', fill_color="#00995c", line_color="black", source=dec_source)

    # set ma line
    ma_legend_items = []
    for ma_name, color in zip(["MA5", "MA10", "MA20", "MA60", "MA120"], Dark2[5]):
        ma_df = df[['index', 'date', 'close', 'open', 'high', 'low', 'volume', ma_name]]
        source = ColumnDataSource(ma_df)
        ma_line = p1.line(x="index", y=ma_name, line_width=2, color=color, alpha=0.8,
                          muted_color=color, muted_alpha=0.9, source=source)
        ma_legend_items.append((ma_name, [ma_line]))

    # set ma legend
    legend = Legend(items=ma_legend_items, location=(0, 250))
    p1.add_layout(legend, 'left')

    # set twinx for volume
    y2_start = df['volume'].min() * 0.95
    y2_end = df['volume'].max() * 2
    p1.extra_y_ranges = {"vol": Range1d(y2_start, y2_end)}
    p1.vbar('index', 0.5, 'volume', y_range_name='vol', color='blue', alpha=0.2, source=df_source)
    p1.add_layout(LinearAxis(y_range_name="vol" ,axis_label="vol"), 'right')

    # RSI Chart
    rsi_df = pd.DataFrame(stock_data['RSI']).reset_index().rename(columns={'index': 'date'})
    kd_df = pd.DataFrame(stock_data['STOCH']).reset_index().rename(columns={'index': 'date'})
    rsi_kd_df = pd.concat([rsi_df, kd_df], axis=1)
    rsi_source = ColumnDataSource(rsi_kd_df)

    rsi_kd_legend_items = []
    for index_name, color in zip(["RSI_12", "RSI_36", "slowk", "slowd"], Spectral4):
        index_line = p2.line('index', index_name, line_width=3, color=color, alpha=0.8, muted_color=color,
                             muted_alpha=0.2, source=rsi_source)

        rsi_kd_legend_items.append((index_name, [index_line]))

    # set rsi_kd legend
    legend = Legend(items=rsi_kd_legend_items, location=(0, 50))
    p2.add_layout(legend, 'left')

    # MACD Chart
    macd = pd.DataFrame(stock_data['MACD']).reset_index().rename(columns={'index': 'date'})
    macd = macd.reset_index()
    macd_source = ColumnDataSource(macd)

    macd_legend_items = []
    for index_name, color in zip(["macd", "macdsignal", "macdhist"], Dark2[3]):
        if index_name == "macdhist":
            index_line = p3.vbar('index', 0.5, index_name, color=color, alpha=0.8, muted_color=color, muted_alpha=0.2,
                                 source=macd_source)
        else:
            index_line = p3.line('index', index_name, line_width=3, color=color, alpha=0.8, muted_color=color,
                                 muted_alpha=0.2, source=macd_source)

        macd_legend_items.append((index_name, [index_line]))

    # set macd legend
    legend = Legend(items=macd_legend_items, location=(0, 50))
    p3.add_layout(legend, 'left')

    # set legend mode
    for fig in [p1, p2, p3]:
        # set legend
        fig.legend.label_text_font_size = '8pt'
        # use hide or mute
        fig.legend.click_policy = "hide"
        #     fig.add_layout(legend, 'left')
    
    # use brower output
#     output_file("candlestick.html", title="candlestick.py example")
    # use jupyter output
    output_notebook()
    # use columns to control all fig  locations,you could try row method.
    show(column(p1, p2, p3))

In [17]:
#open 2330 TSMC 台積電 demo_file
route=os.getcwd()+'/2330_tw_price.json'
with open(route, 'r') as outfile:
    test=json.load(outfile)

# run code
technical_chart(test)

Loading BokehJS ...

In [18]:
from backtesting import Backtest, Strategy
from backtesting.lib import crossover

from backtesting.test import SMA, GOOG


class SmaCross(Strategy):
    n1 = 10
    n2 = 20

    def init(self):
        close = self.data.Close
        self.sma1 = self.I(SMA, close, self.n1)
        self.sma2 = self.I(SMA, close, self.n2)

    def next(self):
        if crossover(self.sma1, self.sma2):
            self.buy()
        elif crossover(self.sma2, self.sma1):
            self.sell()


bt = Backtest(GOOG, SmaCross,
              cash=10000, commission=.002,
              exclusive_orders=True)

output = bt.run()
bt.plot()

C:\Users\user\miniconda3\lib\site-packages\backtesting\_plotting.py:50: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

Row(id='3886', ...)

In [19]:
import numpy as np

from bokeh.layouts import row
from bokeh.models import BoxAnnotation, CustomJS
from bokeh.plotting import figure

N = 4000

x = np.random.random(size=N) * 100
y = np.random.random(size=N) * 100
radii = np.random.random(size=N) * 1.5
colors = [
    "#%02x%02x%02x" % (int(r), int(g), 150) for r, g in zip(50+2*x, 30+2*y)
]

box = BoxAnnotation(left=0, right=0, bottom=0, top=10,
    fill_alpha=0.1, line_color='black', fill_color='black')

jscode = """
    box[%r] = cb_obj.start
    box[%r] = cb_obj.end
"""

p1 = figure(title='Pan and Zoom Here', x_range=(0, 100), y_range=(0, 100),
            tools='box_zoom,wheel_zoom,pan,reset', width=400, height=400)
p1.scatter(x, y, radius=radii, fill_color=colors, fill_alpha=0.6, line_color=None)

xcb = CustomJS(args=dict(box=box), code=jscode % ('left', 'right'))
ycb = CustomJS(args=dict(box=box), code=jscode % ('bottom', 'top'))

p1.x_range.js_on_change('start', xcb)
p1.x_range.js_on_change('end', xcb)
p1.y_range.js_on_change('start', ycb)
p1.y_range.js_on_change('end', ycb)

p2 = figure(title='See Zoom Window Here', x_range=(0, 100), y_range=(0, 100),
            tools='', width=400, height=400)
p2.scatter(x, y, radius=radii, fill_color=colors, fill_alpha=0.6, line_color=None)
p2.add_layout(box)

layout = row(p1, p2)

show(layout)